## Importing packages

In [20]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt 
import seaborn as sns
import json
import math

#import geopandas as gpd

import pgeocode
from geopy.geocoders import Nominatim

import folium
import folium.plugins as plugins

from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster, HeatMapWithTime


from pandas.io.json import json_normalize
from geopy.geocoders import Nominatim 
import requests

## Cleaning Data (snapchat)

In [21]:
location = json.loads(open("data/location_history.json").read())
areas_visited = location['Location History']

location_list = list()

for j in range(len(areas_visited)):
    location_list.append([areas_visited[j]['Time'], areas_visited[j]['Latitude, Longitude']])

location_df = pd.DataFrame (location_list, columns = ['Time', 'Latitude, Longitude'])

location_df[['Latitude_old', 'Longitude_old']] = location_df['Latitude, Longitude'].str.split(',', expand=True)
location_df[['lat', 'Lat_throw']] = location_df['Latitude_old'].str.split('±', expand=True)
location_df[['long', 'Long_throw']] = location_df['Longitude_old'].str.split('±', expand=True)
location_df = location_df.drop(['Latitude_old', 'Longitude_old', 'Latitude, Longitude', 'Lat_throw', 'Long_throw'], axis=1)

location_df['lat'] = pd.to_numeric(location_df['lat'])
location_df['long'] = pd.to_numeric(location_df['long'])

location_df

Time     lat    long
0     2021/12/08 21:02:19 UTC  42.275 -83.734
1     2021/12/08 21:02:19 UTC  42.275 -83.735
2     2021/12/08 21:51:58 UTC  42.275 -83.734
3     2021/12/08 21:51:58 UTC  42.275 -83.734
4     2021/12/08 23:00:01 UTC  42.275 -83.734
...                       ...     ...     ...
2300  2022/03/08 03:28:39 UTC  42.275 -83.734
2301  2022/03/08 03:43:42 UTC  42.275 -83.734
2302  2022/03/08 03:44:56 UTC  42.275 -83.734
2303  2022/03/08 03:45:14 UTC  42.275 -83.734
2304  2022/03/08 05:03:10 UTC  42.276 -83.734

[2305 rows x 3 columns]

## Timelapse Map

In [28]:
selected_columns = location_df[["Time", "lat", "long"]]
timelapse_df = selected_columns.copy()

lat_long_list = []
for i in timelapse_df['Time'].unique():
    temp=[]
    for index, instance in timelapse_df[timelapse_df['Time'] == i].iterrows():
        temp.append([instance['lat'],instance['long']])
    lat_long_list.append(temp)
    
#converting it to datetime format
timelapse_df['Time']= pd.to_datetime(timelapse_df['Time'])

#creating a time index
time_index = []
for i in timelapse_df['Time'].unique():
    time_index.append(i)
#formatting the index
date_strings = [d.strftime('%d/%m/%Y, %H:%M:%S') for d in time_index]

# -------------------------------------------------------------------------------------#

#Choosing the map type 
timelapse_map = folium.Map(location=[42.2808, -83.7430],zoom_start = 5, tiles="openstreetmap",attr="Stadia.AlidadeSmoothDark")
#Plot it on the map
HeatMapWithTime(lat_long_list,radius=10,auto_play=True,position='bottomright',name="cluster",index=date_strings,max_opacity=0.7).add_to(timelapse_map)
# Display the map

# Adds tool to the top right
from folium.plugins import MeasureControl
timelapse_map.add_child(MeasureControl())

timelapse_map

## Cluster Map

In [29]:
# Create the map
cluster_map = folium.Map(location=[42.2808, -83.7430], tiles='openstreetmap', zoom_start=5)

# Add points to the map
mc = MarkerCluster()
for idx, row in location_df.iterrows():
    if not math.isnan(row['long']) and not math.isnan(row['lat']):
        mc.add_child(Marker([row['lat'], row['long']]))
cluster_map.add_child(mc)

# Adds tool to the top right
from folium.plugins import MeasureControl
cluster_map.add_child(MeasureControl())

# Display the map
cluster_map

## Foursquare code w/o specific query

In [30]:
CLIENT_ID = 'PDLBYPAUCNCTOCDJ0MHINYM5X2MM5QLJUNBVV2JUNQPKWYPW' # your Foursquare ID
CLIENT_SECRET = 'FEI04Q3MFOROEJWTFW20V0ZOFVYOLLXZIZUJCLR1R2TCL3TU' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 100

In [33]:
ndf = location_df[['lat','long']]
nndf = ndf.drop_duplicates(subset=['long', 'lat'])

concat_df = pd.DataFrame()

for index, row in nndf.iterrows():
    url = "https://api.foursquare.com/v3/places/nearby?ll={},{}&limit=5".format(round(row['lat'], 2),round(row['long'], 2))
#     print(url)
    headers = {
    "Accept": "application/json",
    "Authorization": "fsq3chVTJib0Z11IA8qFisvs8p7dkOJ6ky0WEbGTZ9FQPqc="
    }
    result = requests.request("GET", url, headers=headers).json()
    result_df = json_normalize(result['results'])
    result_df = result_df.rename(columns={"geocodes.main.latitude": "lat", "geocodes.main.longitude": "long", "location.formatted_address": "address"})
#     print(result_df)
    concat_df = concat_df.append(result_df)
    
    
# -------------------------------------------------------------------------------- #

    
foursquare_map_no_query = folium.Map(location=[42.2808, -83.7430], zoom_start=7)
# add a red circle marker to represent each visited locations
for lat, long in zip(nndf.lat, nndf.long):
    folium.features.CircleMarker(
        [lat, long],
        radius=10,
        color='red',
        #popup=label,
        fill = True,
        fill_color='red',
        fill_opacity=0.6
    ).add_to(foursquare_map_no_query)
# add all venues as blue circle markers
for lat, long, label in zip(concat_df.lat, concat_df.long, concat_df.name):
    folium.features.CircleMarker(
        [lat, long],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(foursquare_map_no_query)
# Adds tool to the top right
from folium.plugins import MeasureControl
foursquare_map_no_query.add_child(MeasureControl())

<ipython-input-33-80aaa21ee4c2>:14: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  result_df = json_normalize(result['results'])


In [34]:
concat_df = concat_df[['name', 'distance']]
concat_df

name  distance
0      University of Michigan School of Public Health        63
1          U of M School Of Public Health Building II        58
2                                       Mosher-Jordan       117
3   C.S. Mott Children's Hospital & Von Voigtlande...       264
4                                   Observatory Lodge        72
..                                                ...       ...
0      University of Michigan School of Public Health        63
1          U of M School Of Public Health Building II        58
2                                       Mosher-Jordan       117
3   C.S. Mott Children's Hospital & Von Voigtlande...       264
4                                   Observatory Lodge        72

[958 rows x 2 columns]

In [35]:
print('Red dots represent each visited locations and Blue dots represent surrounding popular venues')

Red dots represent each visited locations and Blue dots represent surrounding popular venues


## Foursquare code w/ specific query

In [36]:
user_input = input()

japanese


In [37]:
concat_df2 = pd.DataFrame()
for index, row in nndf.iterrows():
    url = "https://api.foursquare.com/v3/places/search?query={}&ll={},{}&radius=50000&limit=5".format(user_input, row['lat'], row['long'])
#     print(url)
    headers = {
    "Accept": "application/json",
    "Authorization": "fsq3chVTJib0Z11IA8qFisvs8p7dkOJ6ky0WEbGTZ9FQPqc="
    }
    result = requests.request("GET", url, headers=headers).json()
    result_df = json_normalize(result['results'])
    result_df = result_df.rename(columns={"geocodes.main.latitude": "lat", "geocodes.main.longitude": "long", "location.formatted_address": "address"})
#     print(result_df)
    concat_df2 = concat_df2.append(result_df)
    
concat_df2 = concat_df2.dropna(subset=['lat', 'long', 'name'])


# -------------------------------------------------------------------------------- #


foursquare_map_with_query = folium.Map(location=[42.2808, -83.7430], zoom_start=7)
# add a red circle marker to represent each visited locations
for lat, long in zip(nndf.lat, nndf.long):
    folium.features.CircleMarker(
        [lat, long],
        radius=10,
        color='red',
        #popup=label,
        fill = True,
        fill_color='red',
        fill_opacity=0.6
    ).add_to(foursquare_map_with_query)
# # add all venues as blue circle markers
for lat, long, label in zip(concat_df2.lat, concat_df2.long, concat_df2.name):
    folium.features.CircleMarker(
        [lat, long],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(foursquare_map_with_query)
    
foursquare_map_with_query

<ipython-input-37-6fe537569a92>:10: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  result_df = json_normalize(result['results'])


In [39]:
concat_df2 = concat_df2[['name', 'distance']]
concat_df2

name  distance
0                     Poke Fish      4246
1                        Totoro       763
2   Yotsuba Japanese Restaurant      4876
3      Miki Japanese Restaurant      1569
4                       Ajishin     31738
..                          ...       ...
0                     Poke Fish      4424
1                        Totoro       641
2   Yotsuba Japanese Restaurant      5023
3      Miki Japanese Restaurant      1514
4                       Ajishin     31364

[1020 rows x 2 columns]

In [40]:
print('Red dots represent each visited locations and Blue dots represent surrounding popular venues')

Red dots represent each visited locations and Blue dots represent surrounding popular venues


## Popular Venues at Each Location Table

In [42]:
sumdf = location_df[['lat','long']]
sumdf = ndf.drop_duplicates()

new = concat_df['name'].to_frame()

venue1 = new.loc[0]['name'].to_list()
venue2 = new.loc[1]['name'].to_list()
venue3 = new.loc[2]['name'].to_list()

sumdf["1st most Popular Venue"] = venue1
sumdf["2nd most Popular Venue"] = venue2
sumdf["3rd most Popular Venue"] = venue3

sumdf = sumdf.reset_index(drop=True)
sumdf

<ipython-input-42-b241116bd107>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sumdf["1st most Popular Venue"] = venue1
<ipython-input-42-b241116bd107>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sumdf["2nd most Popular Venue"] = venue2
<ipython-input-42-b241116bd107>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stabl

lat    long                          1st most Popular Venue  \
0    42.275 -83.734  University of Michigan School of Public Health   
1    42.275 -83.735                       202 South Thayer Building   
2    42.275 -83.733  University of Michigan School of Public Health   
3    42.277 -83.736                       202 South Thayer Building   
4    42.277 -83.735                       202 South Thayer Building   
..      ...     ...                                             ...   
199  42.278 -83.740                       202 South Thayer Building   
200  42.276 -83.738                       202 South Thayer Building   
201  42.276 -83.733  University of Michigan School of Public Health   
202  42.277 -83.732  University of Michigan School of Public Health   
203  42.279 -83.733  University of Michigan School of Public Health   

                                2nd most Popular Venue 3rd most Popular Venue  
0           U of M School Of Public Health Building II          Mosher-Jordan  
1    University of Michigan Institute for the Human...           CVS Pharmacy  
2           U of M School Of Public Health Building II          Mosher-Jordan  
3    University of Michigan Institute for the Human...           CVS Pharmacy  
4    University of Michigan Institute for the Human...           CVS Pharmacy  
..                                                 ...                    ...  
199  University of Michigan Institute for the Human...           CVS Pharmacy  
200  University of Michigan Institute for the Human...           CVS Pharmacy  
201         U of M School Of Public Health Building II          Mosher-Jordan  
202         U of M School Of Public Health Building II          Mosher-Jordan  
203         U of M School Of Public Health Building II          Mosher-Jordan  

[204 rows x 5 columns]